In [0]:
# read training data

tmp_dir <- tempdir()
compressed_file <- file.path(tmp_dir, "20news.tgz")   # name to be given to the downloaded file
uncompressed_dir  <- file.path(tmp_dir, "20news")    # name to be given to a directory where the files are extracted

In [0]:
download.file("http://qwone.com/~jason/20Newsgroups/20news-bydate-matlab.tgz",
              destfile = compressed_file)

In [3]:
untar(compressed_file, exdir = uncompressed_dir)
list.files(uncompressed_dir)

[1] "20news-bydate"

In [4]:
Twentynews_bydate_dir <- file.path(uncompressed_dir, "20news-bydate")
list.files(Twentynews_bydate_dir )

[1] "matlab"

In [5]:
Twentynews_bydate_matlab_dir <- file.path(Twentynews_bydate_dir, "matlab")
list.files(Twentynews_bydate_matlab_dir )

[1] "test.data"   "test.label"  "test.map"    "train.data"  "train.label"
[6] "train.map"

In [6]:
setwd(Twentynews_bydate_matlab_dir)

train.data <- read.table("train.data")
names(train.data) <- c("docNo","word","count")
head(train.data)
train.label <- read.table("train.label")
names(train.label) <- c("cat")

cat <- train.label$cat[ train.data$docNo ]
train <- data.frame(cat=cat,word=train.data$word,count=train.data$count)
head(train)
tail(train)

# read test data
test.data <- read.table("test.data")
names(test.data) <- c("docNo","word","count")
head(test.data)
test.label <- read.table("test.label")
names(test.label) <- c("cat")

cat <- test.label$cat[ test.data$docNo ]
test <- data.frame(cat=cat,docNo=test.data$docNo,word=test.data$word,count=test.data$count)
head(test)
tail(test)

docNo word count
1 1     1     4   
2 1     2     2   
3 1     3    10   
4 1     4     4   
5 1     5     2   
6 1     6     1

cat word count
1 1   1     4   
2 1   2     2   
3 1   3    10   
4 1   4     4   
5 1   5     2   
6 1   6     1

cat word  count
1467340 20  30181 1    
1467341 20  47387 1    
1467342 20  48339 1    
1467343 20  48919 1    
1467344 20  51544 1    
1467345 20  53958 1

docNo word count
1 1      3   1    
2 1     10   1    
3 1     12   8    
4 1     17   1    
5 1     23   8    
6 1     27   1

cat docNo word count
1 1   1      3   1    
2 1   1     10   1    
3 1   1     12   8    
4 1   1     17   1    
5 1   1     23   8    
6 1   1     27   1

cat docNo word  count
967869 20  7505  40730 1    
967870 20  7505  44515 1    
967871 20  7505  47720 1    
967872 20  7505  50324 1    
967873 20  7505  59935 1    
967874 20  7505  61188 2

In [0]:
# 
trainA <- array( 1, dim=c(max(train$cat), max(train$word, test$word) ) )
for ( i in 1:length(train[,1]) ) {
  trainA[train$cat[i],train$word[i] ] <- trainA[train$cat[i],train$word[i] ] + train$count[i]
}

catMaxN <- max(train$cat)

trainCatN <- as.vector( table(train$cat) )
trainCatProb <- 1/trainCatN
trainCatWordN <- apply(trainA,1,sum)
trainCatWordProb <- diag( 1/trainCatWordN ) %*% trainA

trainCatProbLog <- log(trainCatProb)
trainCatWordProbLog <- log(trainCatWordProb)

# learning is over


In [8]:

# now the tests

testByDocNo <- split(test,test$docNo)
length(testByDocNo)      ## number of test documents
length(testByDocNo[[1]]) ## number of different words in the first document

probListByCat <- function (docNIndexinTest) 
  unlist(
    lapply(1:catMaxN, function (c)
      trainCatProbLog[c] + 
        sum( testByDocNo[[docNIndexinTest]]$count * 
               trainCatWordProbLog[ c, testByDocNo[[docNIndexinTest]]$word ] )
  ))


predictedCat <- 
  apply( array(1:length(testByDocNo)), 1,
    function (x) which.max( probListByCat(x) )
  )

correctCat <- 
  apply( array(1:length(testByDocNo)), 1,
    function (x) testByDocNo[[x]]$cat[1]
  )
  


compare <- data.frame( predicted=predictedCat, correct=correctCat )
# confusion matrix
(cm <- table(compare))


nCorrectDoc <- sum(diag(cm))
nTestDoc <- length(testByDocNo)

# 
(accuracy <- nCorrectDoc/nTestDoc )


[1] 7505

[1] 4

         correct
predicted   1   2   3   4   5   6   7   8   9  10  11  12  13  14  15  16  17
       1  237   3   3   0   0   0   0   1   0   4   2   0   2  10   3   7   2
       2    0 299  33   8   8  42   9   1   1   1   0   5  18   7   8   2   0
       3    0   7 208  15  10   8   4   0   0   0   0   1   0   1   0   1   0
       4    0  12  58 306  38  10  49   2   0   1   0   1  28   3   0   0   0
       5    0   7  11  21 275   2  21   0   0   1   0   2   8   0   0   1   1
       6    1  21  30   2   3 306   1   1   0   2   0   1   3   0   2   2   0
       7    0   1   0   4   4   1 227   5   1   3   1   1   1   1   0   0   2
       8    0   3   2   6   4   0  32 356  25   3   1   0   9   3   0   0   2
       9    0   1   2   0   1   2   5   4 353   1   0   0   2   0   1   0   1
       10   0   0   2   0   1   1   0   2   2 345   4   0   0   2   0   0   1
       11   1   0   1   1   0   0   1   0   0  16 381   0   0   0   1   0   0
       12   1  16  17   5   5  10   3   1   1  

[1] 0.782012